# Alineación de Preferencias con Optimización de Preferencia Directa (Direct Preference Optimization (DPO))

Este notebook te guiará a través del proceso de fine-tuning de un modelo de lenguaje utilizando Optimización de Preferencia Directa (Direct Preference Optimization (DPO)). Usaremos el modelo SmolLM2-135M-Instruct, que ya ha pasado por un entrenamiento SFT, por lo que es compatible con DPO. También puedes usar el modelo que entrenaste en [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb).

<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; color:black'>
     <h2 style='margin: 0;color:blue'>Ejercicio: Alineando SmolLM2 con DPOTrainer</h2>
     <p>Toma un dataset del Hub de Hugging Face y alinea un modelo sobre él.</p> 
     <p><b>Niveles de dificultad</b></p>
     <p>🐢 Usa el dataset `trl-lib/ultrafeedback_binarized`</p>
     <p>🐕 Prueba el dataset `argilla/ultrafeedback-binarized-preferences`</p>
     <p>🦁 Selecciona un dataset relacionado con un caso de uso real que te interese, o usa el modelo que entrenaste en 
        <a href="../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb">1_instruction_tuning</a></p>
</div>


In [ ]:
# Instala los requisitos en Google Colab
# !pip install transformers datasets trl huggingface_hub

# Autenticación en Hugging Face

from huggingface_hub import login

login()

# Para conveniencia, puedes crear una variable de entorno que contenga tu token de Hugging Face como HF_TOKEN

## Importa las libraries


In [ ]:
import torch
import os
from transformers import AutoModelForCausalLM, AutoTokenizer
from datasets import load_dataset
from trl import DPOTrainer, DPOConfig

## Formatea el conjunto de datos

In [ ]:
# Carga el conjunto de datos

# TODO: 🦁🐕 cambia el conjunto de datos a uno de tu elección
dataset = load_dataset(path="trl-lib/ultrafeedback_binarized", split="train")

In [ ]:
# TODO: 🐕 Si tu dataset no está representado como listas de conversaciones, puedes usar la función process_dataset para convertirlo.

**Selecciona el modelo**

Usaremos el modelo SmolLM2-135M-Instruct, que ya ha pasado por un entrenamiento SFT, por lo que es compatible con DPO. También puedes usar el modelo que entrenaste en [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb).

<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; width:80%; color:black'>
     <p>🦁 cambia la ruta del modelo o el ID del repositorio del modelo que entrenaste en <a href="../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb">1_instruction_tuning</a></p>
</div>

In [ ]:
# TODO: 🦁 cambia la ruta del modelo o el ID del repositorio del modelo que entrenaste en [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb)

model_name = "HuggingFaceTB/SmolLM2-135M-Instruct"

device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps" if torch.backends.mps.is_available() else "cpu"
)

# Modelo para afinar
model = AutoModelForCausalLM.from_pretrained(
    pretrained_model_name_or_path=model_name,
    torch_dtype=torch.float16,
).to(device)
model.config.use_cache = False
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token

# Establece el nombre para el modelo afinado que se guardará y/o subirá
finetune_name = "SmolLM2-FT-DPO"
finetune_tags = ["smol-course", "module_2"]

## Train model with DPO

In [ ]:
# Argumentos de entrenamiento
training_args = DPOConfig(
    # Tamaño del lote de entrenamiento por GPU
    per_device_train_batch_size=4,
    # Número de pasos de actualización para acumular antes de realizar una pasada hacia atrás/actualización
    # Tamaño efectivo del lote = per_device_train_batch_size * gradient_accumulation_steps
    gradient_accumulation_steps=4,
    # Ahorra memoria no almacenando activaciones durante la pasada hacia adelante
    # En su lugar, las vuelve a calcular durante la pasada hacia atrás
    gradient_checkpointing=True,
    # Tasa base de aprendizaje para el entrenamiento
    learning_rate=5e-5,
    # Tipo de programación de la tasa de aprendizaje - 'coseno' disminuye gradualmente la LR siguiendo una curva coseno
    lr_scheduler_type="cosine",
    # Número total de pasos de entrenamiento
    max_steps=200,
    # Desactiva el guardado de puntos de control del modelo durante el entrenamiento
    save_strategy="no",
    # Con qué frecuencia registrar métricas de entrenamiento
    logging_steps=1,
    # Directorio para guardar las salidas del modelo
    output_dir="smol_dpo_output",
    # Número de pasos para el calentamiento de la tasa de aprendizaje
    warmup_steps=100,
    # Usar precisión bfloat16 para un entrenamiento más rápido
    bf16=True,
    # Desactivar los registros de wandb/tensorboard
    report_to="none",
    # Mantener todas las columnas en el dataset incluso si no se utilizan
    remove_unused_columns=False,
    # Habilitar MPS (Metal Performance Shaders) para dispositivos Mac
    use_mps_device=device == "mps",
    # ID del modelo para cargas al HuggingFace Hub
    hub_model_id=finetune_name,
)

In [ ]:
trainer = DPOTrainer(
    # El modelo a ser entrenado
    model=model,
    # Configuración de entrenamiento de los argumentos anteriores
    args=training_args,
    # Dataset que contiene los pares de respuestas preferidas/rechazadas
    train_dataset=dataset,
    # Tokenizer para procesar las entradas
    processing_class=tokenizer,
    # Parámetro específico de DPO que controla la intensidad del modelo de preferencias
    # Valores más bajos (como 0.1) hacen que el modelo sea más conservador al seguir las preferencias
    beta=0.1,
    # Longitud máxima del prompt de entrada en tokens
    max_prompt_length=1024,
    # Longitud máxima combinada de prompt + respuesta en tokens
    max_length=1536,
)

In [ ]:
# Entrena el modelo
trainer.train()

# Guarda el modelo
trainer.save_model(f"./{finetune_name}")

# Sube el modelo a Hugging Face si el inicio de sesión o HF_TOKEN está configurado
if os.getenv("HF_TOKEN"):
    trainer.push_to_hub(tags=finetune_tags)

## 💐 ¡Has terminado!

Este notebook proporcionó una guía paso a paso para realizar fine-tuning al modelo `HuggingFaceTB/SmolLM2-135M` utilizando el `DPOTrainer`. Siguiendo estos pasos, puedes adaptar el modelo para realizar tareas específicas de manera más eficaz. Si deseas continuar trabajando en este curso, aquí tienes algunos pasos que podrías intentar:

- Prueba este notebook en una dificultad más alta
- Revisa el PR de un compañero
- Mejora el material del curso a través de un Issue o PR.
